In [41]:
# I. Setup: Import Libraries and Define Constants
# ==============================================
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import re
import os
import warnings

In [42]:
# --- Load the dataset ---
# Suppress minor warnings if necessary (e.g., future warnings from libraries)
warnings.simplefilter(action='ignore', category=FutureWarning)

# Define constants based on the report (e.g., file paths, specific values)
# Note: Replace 'path/to/your/data/' with the actual path
# --- USER ACTION REQUIRED: Update DATA_DIR and file names ---
DATA_DIR = 'C:/Users/jason/OneDrive - The Pennsylvania State University/DAAN 881, Data Drive Decision Making/Project/Auto Data/MI/' # Example path
RAW_CRASH_FILE_CSV = os.path.join(DATA_DIR, 'Michigan_CrashDataset_2022.csv') # Original CSV name from user code
RAW_CRASH_FILE_XLSX = os.path.join(DATA_DIR, 'Michigan_CrashDataset_2022.xlsx') # Original Excel name from user code
OUTPUT_DIR = 'C:/Users/jason/OneDrive - The Pennsylvania State University/DAAN 881, Data Drive Decision Making/Project/Deliverable 4/' # Directory to save plots

# Ensure output directory exists
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

In [43]:
# -------------------------------------------
# II. Data Loading
# -------------------------------------------
try:
    df_raw = pd.read_csv(RAW_CRASH_FILE_CSV, low_memory=False)
    print(f"Successfully loaded CSV: {RAW_CRASH_FILE_CSV}")
except FileNotFoundError:
    print(f"CSV not found. Attempting Excel...")
    try:
        df_raw = pd.read_excel(RAW_CRASH_FILE_XLSX)
        print(f"Successfully loaded Excel: {RAW_CRASH_FILE_XLSX}")
    except Exception as e:
        print(f"Error loading from Excel: {e}")
        raise
except Exception as e:
    print(f"Error loading CSV: {e}")
    # Attempt fallback to Excel or handle further
    raise

print("Initial raw shape:", df_raw.shape)

Successfully loaded CSV: C:/Users/jason/OneDrive - The Pennsylvania State University/DAAN 881, Data Drive Decision Making/Project/Auto Data/MI/Michigan_CrashDataset_2022.csv
Initial raw shape: (364105, 154)


In [44]:
# -------------------------------------------
# III. Initial Filtering: Keep Motor Vehicle Drivers
# -------------------------------------------
party_type_col = "Party Type"  # as determined from data dictionary
driver_party_type_value = "Motor Vehicle Driver"
if party_type_col in df_raw.columns:
    df = df_raw[df_raw[party_type_col] == driver_party_type_value].copy()
    df.reset_index(drop=True, inplace=True)
    print(f"Filtered for '{driver_party_type_value}'. New shape:", df.shape)
else:
    print(f"Warning: No '{party_type_col}' column found. Using entire dataset.")
    df = df_raw.copy()

if df.empty:
    raise ValueError("No data after driver filtering. Check 'Party Type' col or value.")

Filtered for 'Motor Vehicle Driver'. New shape: (305786, 154)


In [45]:
# -------------------------------------------
# IV. Create Unique IDs (AccidentID, PersonID)
# -------------------------------------------
grouping_cols = ["Crash Year","Crash Month","Crash Day","Time of Day","County","City or Township"]
missing_grouping = [g for g in grouping_cols if g not in df.columns]
if missing_grouping:
    print(f"Warning: Missing grouping columns: {missing_grouping} - AccidentID may not be fully unique.")

df["AccidentID"] = df.groupby([g for g in grouping_cols if g in df.columns], dropna=False).ngroup()
df.reset_index(drop=True, inplace=True)
df["PersonID"] = df.index

In [46]:
# -------------------------------------------
# V. Select Key Columns
# -------------------------------------------
COLUMNS_TO_KEEP = [
    # IDs
    "AccidentID","PersonID",
    # Crash info
    "Crash Year","Crash Month","Crash Day","Day of Week","Time of Day",
    # Location
    "County","City or Township","Rural/Urban Area (2016+)","Highway Class",
    # Crash severity
    "Worst Injury in Crash","Crash Type","Crash: Fatal Crash","Crash: Injury Crash",
    "Crash: Property Damage",
    # Party & person
    "Party Type","Person Age","Person Gender","Person Race (2021+)",
    "Person Degree of Injury",
    # Driver conditions
    "Driver Condition: Emotional (2016+)","Driver Condition: Fatigued or Asleep (2016+)",
    "Driver Condition: Medication","Driver Condition: Normal","Driver Condition: Other (2016+)",
    "Driver Condition: Physically Disabled (2016+)","Driver Condition: Sick",
    "Driver Contributing Factor - Alcohol Use (2016+)","Driver Contributing Factor - Drug Use (2016+)",
    "Crash: Drinking","Crash: Drug Use","Drugs Suspected","Contributing Circumstance 1 (2016+)",
    "Contributing Circumstance 2 (2016+)",
    # Substance testing
    "Test Offered - Alcohol","Test Offered - Drug (2016+)",
    "Refusal Information - Alcohol","Refusal Information - Drug (2016+)",
    "Test Result - Alcohol","Test Result - Cannabinoid Drug (2021+)",
    "Test Result - Drug 1","Test Result - Drug 2","Test Result - Drug 3",
    "Test Result Pending - Alcohol (2016+)","Test Result Pending - Drug (2016+)",
    # Environmental
    "Lighting Conditions","Road Conditions","Weather Conditions (2016+)",
    "Traffic Control","Posted Speed Limit",
    # Vehicle/occupant
    "Person Position","Person Trapped","Person Ejection","Person Restraint (2016+)",
    "Traffic Unit Type","Vehicle Model Year","Vehicle Type","Extent of Damage (2015+)"
]

keep_existing = [c for c in COLUMNS_TO_KEEP if c in df.columns]
missing_expected = [c for c in COLUMNS_TO_KEEP if c not in df.columns]
if missing_expected:
    print("Warning: The following expected columns do not exist:", missing_expected)

df = df[keep_existing].copy()
print("Shape after selecting relevant columns:", df.shape)

Shape after selecting relevant columns: (305786, 59)


In [47]:
# -------------------------------------------
# VI. Data Cleaning & Transformation
# -------------------------------------------

## A. Basic Standardization (string columns)
string_cols = df.select_dtypes(include=["object"]).columns
for col in string_cols:
    # Convert to str, strip whitespace, unify "nan" -> actual NaN
    df[col] = df[col].astype(str).str.strip().replace({"nan": np.nan, "none": np.nan})
    # We can unify to Title-case or Lower-case
    # Example using Title-case to preserve typical forms (e.g. "Fatal Injury (K)")
    df[col] = df[col].apply(lambda x: x.title() if isinstance(x,str) else x)

## B. Missing/Invalid Value Handling

### 1) Person Age
if "Person Age" in df.columns:
    # Convert possible "Dob Invalid" to NaN
    df["Person Age"] = df["Person Age"].replace("Dob Invalid", np.nan)
    df["Person Age"] = pd.to_numeric(df["Person Age"], errors="coerce")
    median_age = df["Person Age"].median(skipna=True)
    df["Age_Imputed"] = df["Person Age"].isna().astype(int)
    df["Person Age"].fillna(median_age, inplace=True)
    print(f"Imputed {df['Age_Imputed'].sum()} 'Person Age' values with median {median_age:.1f}")

### 2) Gender / Race
for col in ["Person Gender","Person Race (2021+)"]:
    if col in df.columns:
        df[col] = df[col].replace({"Uncoded & Errors": UNKNOWN_VALUE_CAT, np.nan: UNKNOWN_VALUE_CAT})

### 3) Crash Hour derivation from "Time of Day"
def extract_hour(time_str):
    # fallback
    if pd.isna(time_str):
        return UNKNOWN_VALUE_NUM
    s = str(time_str).strip().lower()
    # check for e.g. "7:00 pm - 7:59 pm"
    if "midnight" in s:
        return 0
    if "noon" in s:
        return 12
    if "-" not in s:
        # Possibly just an hour or unknown
        # try simple parse
        match = re.match(r"(\d{1,2})(am|pm)?", s)
        if match:
            hour_str, ampm = match.groups()
            try:
                hour = int(hour_str)
            except:
                return UNKNOWN_VALUE_NUM
            # handle am/pm if present
            if ampm == "am" and hour == 12: hour = 0
            elif ampm == "pm" and hour < 12: hour += 12
            return hour
        return UNKNOWN_VALUE_NUM

    # parse the first part
    first_part = s.split("-",1)[0].strip()
    match = re.match(r"(\d{1,2}):\d{2}\s*(am|pm)?", first_part)
    if not match:
        return UNKNOWN_VALUE_NUM
    hour_str, ampm = match.groups()
    try:
        hour_num = int(hour_str)
    except:
        return UNKNOWN_VALUE_NUM
    if ampm=="am" and hour_num==12: hour_num=0
    elif ampm=="pm" and hour_num<12: hour_num+=12
    return hour_num

df["Crash Hour"] = df["Time of Day"].apply(extract_hour) if "Time of Day" in df.columns else UNKNOWN_VALUE_NUM

### 4) Numeric placeholders (Posted Speed Limit, Vehicle Model Year)
if "Posted Speed Limit" in df.columns:
    df["Posted Speed Limit"] = pd.to_numeric(df["Posted Speed Limit"], errors="coerce")
    # replace invalid like 0,999 -> NaN
    df["Posted Speed Limit"] = df["Posted Speed Limit"].replace([0,999], np.nan)
    df["Posted Speed Limit"].fillna(UNKNOWN_VALUE_NUM, inplace=True)

if "Vehicle Model Year" in df.columns:
    df["Vehicle Model Year"] = pd.to_numeric(df["Vehicle Model Year"], errors="coerce")
    # e.g. 9999 -> invalid
    df["Vehicle Model Year"] = df["Vehicle Model Year"].replace(9999, np.nan)
    # Future year e.g. > 2023? 
    crash_year = 2022
    df.loc[df["Vehicle Model Year"] > crash_year+1, "Vehicle Model Year"] = np.nan
    df["Vehicle Model Year"].fillna(UNKNOWN_VALUE_NUM, inplace=True)

### 5) Driver condition fields -> map "no" vs. "yes" 
# if they exist, we might unify them to binary flags
condition_cols = [
    "Driver Condition: Emotional (2016+)",
    "Driver Condition: Fatigued Or Asleep (2016+)",
    "Driver Condition: Medication",
    "Driver Condition: Normal",
    "Driver Condition: Other (2016+)",
    "Driver Condition: Physically Disabled (2016+)",
    "Driver Condition: Sick"
]
for c in condition_cols:
    if c in df.columns:
        # E.g., if it's "No" vs "Medication" or "Uncoded & Errors" => unify
        df[c] = df[c].replace({UNKNOWN_VALUE_CAT.lower(): UNKNOWN_VALUE_CAT})
        # The actual mapping depends on data dictionary; for now, we unify "No" => 0, else 1,
        # with special handling if c == "Driver Condition: Normal".
        if c=="Driver Condition: Normal":
            df[c+"_Flag"] = df[c].apply(lambda x: 1 if str(x).strip().lower()=="normal" else 0)
        else:
            df[c+"_Flag"] = df[c].apply(lambda x: 0 if x.strip().lower()=="no" else 1)

### 6) Contributing Factor & Suspected
# Example mapping
contrib_cols = [
    "Driver Contributing Factor - Alcohol Use (2016+)",
    "Driver Contributing Factor - Drug Use (2016+)",
    "Drugs Suspected"
]
for c in contrib_cols:
    if c in df.columns:
        # Example known textual codes
        # e.g. "Alcohol use was a contributing factor" => 1, "Was not" => 0, else -1
        df[c] = df[c].str.lower()
        if "alcohol" in c:
            map_dict = {
                "alcohol use was a contributing factor": 1,
                "alcohol use was not a contributing factor": 0,
                UNKNOWN_VALUE_CAT.lower(): UNKNOWN_VALUE_NUM
            }
        elif "drug use (2016+)" in c:
            map_dict = {
                "drug use was a contributing factor": 1,
                "drug use was not a contributing factor": 0,
                UNKNOWN_VALUE_CAT.lower(): UNKNOWN_VALUE_NUM
            }
        elif "drugs suspected" in c.lower():
            map_dict = {
                "drugs suspected": 1,
                "No Drugs Suspected".lower(): 0,
                UNKNOWN_VALUE_CAT.lower(): UNKNOWN_VALUE_NUM
            }
        else:
            map_dict = {}
        df[c+"_Mapped"] = df[c].map(map_dict).fillna(UNKNOWN_VALUE_NUM).astype(int)

### 7) Crash: Drinking, Crash: Drug Use => binary
for c in ["Crash: Drinking","Crash: Drug Use"]:
    if c in df.columns:
        # e.g. "Drinking Involved" =>1, "No Drinking Involved"=>0
        # if not sure, check the value_counts first
        df[c+"_Flag"] = df[c].apply(lambda x: 1 if "involved" in str(x).lower() else 0)

### 8) Test Offered, Refusal, etc.
offer_cols = ["Test Offered - Alcohol","Test Offered - Drug (2016+)"]
for c in offer_cols:
    if c in df.columns:
        df[c] = df[c].replace({"Uncoded & Errors":"not reported", np.nan:"not reported"})
        df[c+"_Mapped"] = df[c].map({"yes":1, "no":0, "not reported":UNKNOWN_VALUE_NUM}).fillna(UNKNOWN_VALUE_NUM).astype(int)

refusal_cols = ["Refusal Information - Alcohol","Refusal Information - Drug (2016+)"]
for c in refusal_cols:
    if c in df.columns:
        df[c].fillna("no", inplace=True)
        df[c+"_Flag"] = df[c].apply(lambda x: 1 if "refused" in str(x).lower() else 0)

Imputed 17765 'Person Age' values with median 39.0


In [48]:
# -------------------------------------------
# VII. Time-Series Splitting Placeholder
# -------------------------------------------
# We do not fully do it now, but demonstrate the approach:
# Sort by Crash Year, Crash Month, Crash Day => create date col => assign ~70% as train, ~30% as test
# We'll finalize in Deliverable 5, but code is:
if all(x in df.columns for x in ["Crash Year","Crash Month","Crash Day"]):
    # create a pseudo date if we wanted
    # But we won't do the final split, just show how:
    pass

In [49]:
# -------------------------------------------
# VIII. Visualization Examples
# -------------------------------------------
import os
def save_plot(fig, name):
    if fig is not None:
        fname = os.path.join(OUTPUT_DIR, name)
        fig.savefig(fname, dpi=150, bbox_inches="tight")
        plt.close(fig)

print("\nStarting Visualizations...")

# Example Visualization 1: Distribution of "Drug Classes" found
# We check the splitted "Test Result - Drug 1" etc. to see if we can parse them
# In your code, you attempted to parse "Narcotics" vs. "other" from e.g. "Narcotics: Fentanyl".
# We'll replicate a simple version:
def split_drug_result(s):
    if pd.isna(s):
        return UNKNOWN_VALUE_CAT
    st = str(s).lower().strip()
    if ":" in st:
        cls, nm = st.split(":",1)
        return cls.strip()
    else:
        return st if st else UNKNOWN_VALUE_CAT

drug_class_cols = [c for c in df.columns if "Test Result - Drug" in c]
all_drug_classes = pd.Series(dtype=str)
for col in drug_class_cols:
    if col in df.columns:
        parsed = df[col].apply(split_drug_result)
        # filter out negative, unknown_result, refused
        # depends on your logic
        valid_mask = ~parsed.isin(["negative","refused","unknown_result",UNKNOWN_VALUE_CAT.lower()])
        all_drug_classes = pd.concat([all_drug_classes, parsed[valid_mask]])

if not all_drug_classes.empty:
    class_counts = all_drug_classes.value_counts().sort_values(ascending=False)
    if not class_counts.empty:
        fig1, ax1 = plt.subplots(figsize=(8,6))
        sns.barplot(x=class_counts.values, y=class_counts.index, ax=ax1, color="skyblue")
        ax1.set_xlabel("Count of Drivers")
        ax1.set_ylabel("Drug Class")
        ax1.set_title("Drug Classes Among Drivers (Excluding 'Unknown/Negative/Refused')")
        plt.tight_layout()
        save_plot(fig1, "plot_drug_class_distribution.png")
    else:
        print("No valid drug class entries to plot (all unknown/negative).")
else:
    print("No drug class data to plot for Distribution of 'Drug 1/2/3' classes.")

# Example Visualization 2: Crash Severity by Opioid vs. Non-Opioid
group_col = "Opioid_Involvement"  # We can define if we see 'Narcotics' in results. 
# But we did not finalize. Alternatively, use 'Driver Contributing Factor - Drug Use (2016+)_Mapped' 
op_col = "Driver Contributing Factor - Drug Use (2016+)_Mapped"
severity_flags = ["Crash: Fatal Crash","Crash: Injury Crash","Crash: Property Damage"]
if op_col in df.columns and all(sf in df.columns for sf in severity_flags):
    opioid_count = (df[op_col]==1).sum()
    if opioid_count < 5:
        print(f"Warning: Very few opioid_involved cases = {opioid_count}, might skip or produce empty chart.")

    df_plot = df[[op_col]+severity_flags].copy()
    # Convert severity flags to means grouped by op_col
    df_grp = df_plot.groupby(op_col)[severity_flags].mean().reset_index()
    df_grp[op_col] = df_grp[op_col].map({1:"Drug Factor", 0:"No Drug Factor", UNKNOWN_VALUE_NUM:"Unknown"})
    df_melt = df_grp.melt(id_vars=op_col, var_name="Severity", value_name="Proportion")
    fig2, ax2 = plt.subplots(figsize=(8,6))
    sns.barplot(data=df_melt, x=op_col, y="Proportion", hue="Severity", ax=ax2, palette="muted")
    ax2.set_title("Crash Severity: Drug Factor vs. Not (Based on Contributing Factor)")
    ax2.set_xlabel("Drug Use Contributing Factor (Yes/No/Unknown)")
    ax2.set_ylabel("Proportion of Crashes")
    plt.tight_layout()
    save_plot(fig2, "plot_severity_comparison_by_drug_factor.png")
else:
    print("Skipping severity vs. opioid_involvement plot: required columns missing or insufficient data.")

# Additional plots can be added similarly...

print("Visualization Complete.")

# End of consolidated script


Starting Visualizations...


TypeError: agg function failed [how->mean,dtype->object]